In [1]:
import os
import datetime
import csv
import tqdm
import math
import numpy as np
import pandas as pd
import json

import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.autograd import Variable

import data_loader

In [2]:
train_file = "Gowalla_totalCheckins.txt"

ftype = torch.cuda.FloatTensor
ltype = torch.cuda.LongTensor

# Model Hyperparameters
dim = 13    # dimensionality
ww = 360  # winodw width (6h)
up_time = 1440  # 1d
lw_time = 30    # 50m
up_dist = 100   # ??
lw_dist = 1

# Training Parameters
user_cnt = 32899 #50 #107092#0
loc_cnt = 1115406 #50 #1280969#0
reg_lambda = 0.1

# Training Parameters
batch_size = 2
num_epochs = 30
learning_rate = 0.001
momentum = 0.9
evaluate_every = 1
h_0 = Variable(torch.randn(dim, 1), requires_grad=False).type(ftype)


In [3]:

try:
    xrange
except NameError:
    xrange = range

In [4]:
def load_data(train):
    user2id = {}
    poi2id = {}
    id2latilongi = {}

    train_user = []
    train_time = []
    train_lati = []
    train_longi = []
    train_loc = []
    valid_user = []
    valid_time = []
    valid_lati = []
    valid_longi = []
    valid_loc = []
    test_user = []
    test_time = []
    test_lati = []
    test_longi = []
    test_loc = []

    train_f = open(train, 'r')
    lines = train_f.readlines()

    user_time = []
    user_lati = []
    user_longi = []
    user_loc = []
    visit_thr = 30

    prev_user = int(lines[0].split('\t')[0])
    visit_cnt = 0
    for i, line in enumerate(lines):
        tokens = line.strip().split('\t')
        user = int(tokens[0])
        if user==prev_user:
            visit_cnt += 1
        else:
            if visit_cnt >= visit_thr:
                user2id[prev_user] = len(user2id)
            prev_user = user
            visit_cnt = 1

    train_f = open(train, 'r')
    lines = train_f.readlines()

    prev_user = int(lines[0].split('\t')[0])
    for i, line in enumerate(lines):
        tokens = line.strip().split('\t')
        user = int(tokens[0])
        if user2id.get(user) is None:
            continue
        user = user2id.get(user)

        time = (datetime.datetime.strptime(tokens[1], "%Y-%m-%dT%H:%M:%SZ")\
                -datetime.datetime(2009,1,1)).total_seconds()/60  # minutes
        lati = float(tokens[2])
        longi = float(tokens[3])
        location = int(tokens[4])
        if poi2id.get(location) is None:
            poi2id[location] = len(poi2id)
            id2latilongi[len(poi2id)] = [lati, longi]
        location = poi2id.get(location)

        if user == prev_user:
            user_time.insert(0, time)
            user_lati.insert(0, lati)
            user_longi.insert(0, longi)
            user_loc.insert(0, location)
        else:
            train_thr = int(len(user_time) * 0.7)
            valid_thr = int(len(user_time) * 0.8)
            train_user.append(user)
            train_time.append(user_time[:train_thr])
            train_lati.append(user_lati[:train_thr])
            train_longi.append(user_longi[:train_thr])
            train_loc.append(user_loc[:train_thr])
            valid_user.append(user)
            valid_time.append(user_time[train_thr:valid_thr])
            valid_lati.append(user_lati[train_thr:valid_thr])
            valid_longi.append(user_longi[train_thr:valid_thr])
            valid_loc.append(user_loc[train_thr:valid_thr])
            test_user.append(user)
            test_time.append(user_time[valid_thr:])
            test_lati.append(user_lati[valid_thr:])
            test_longi.append(user_longi[valid_thr:])
            test_loc.append(user_loc[valid_thr:])

            prev_user = user
            user_time = [time]
            user_lati = [lati]
            user_longi = [longi]
            user_loc = [location]

    if user2id.get(user) is not None:
        train_thr = int(len(user_time) * 0.7)
        valid_thr = int(len(user_time) * 0.8)
        train_user.append(user)
        train_time.append(user_time[:train_thr])
        train_lati.append(user_lati[:train_thr])
        train_longi.append(user_longi[:train_thr])
        train_loc.append(user_loc[:train_thr])
        valid_user.append(user)
        valid_time.append(user_time[train_thr:valid_thr])
        valid_lati.append(user_lati[train_thr:valid_thr])
        valid_longi.append(user_longi[train_thr:valid_thr])
        valid_loc.append(user_loc[train_thr:valid_thr])
        test_user.append(user)
        test_time.append(user_time[valid_thr:])
        test_lati.append(user_lati[valid_thr:])
        test_loc.append(user_loc[valid_thr:])

    return len(user2id), poi2id, id2latilongi, train_user, train_time, train_lati, train_longi, train_loc, valid_user, valid_time, valid_lati, valid_longi, valid_loc, test_user, test_time, test_lati, test_longi, test_loc

## 保存数据，以便之后的直接调用

In [4]:
user_cnt, poi2id, id2latilongi, train_user, train_time, train_lati, train_longi, train_loc, valid_user, valid_time, valid_lati, valid_longi, valid_loc, test_user, test_time, test_lati, test_longi, test_loc = load_data(train_file)


In [5]:
len(id2latilongi)

1164559

In [11]:
pd.DataFrame.from_dict(id2latilongi, orient="index", columns=['lati','longi']).to_csv("id2latilongi.csv", index=False)

## important

In [5]:
pd.read_csv("id2latilongi.csv")

lati       longi
0        30.235909  -97.795140
1        30.269103  -97.749395
2        30.255731  -97.763386
3        30.263418  -97.757597
4        30.274292  -97.740523
5        30.261599  -97.758581
6        30.267910  -97.749312
7        30.281120  -97.745211
8        40.643885  -73.782806
9        40.741374  -73.988105
10       40.741388  -73.989455
11       40.724910  -73.994621
12       40.729768  -73.998535
13       40.728527  -73.996868
14       40.741747  -73.993421
15       40.734193  -74.004164
16       40.742512  -74.006031
17       40.742396  -74.007543
18       40.735885  -74.004968
19       40.727525  -73.985399
20       40.756880  -73.986225
21       40.707417  -74.011363
22       40.707173  -74.010545
23       40.707071  -74.011953
24       40.705823  -73.996696
25       40.769378  -73.963083
26       40.780805  -73.976473
27       40.731724  -74.003338
28       40.730869  -73.997566
29       40.742201  -73.987995
...            ...         ...
1164529  51.999576    8.502936
1164530  51.991815    8.493454
1164531  51.989664    8.506508
1164532  52.023326    8.527240
1164533  53.552376   10.006782
1164534  53.795523    9.428444
1164535  54.754836    8.288261
1164536  13.823481  100.558398
1164537  13.765701  100.537731
1164538   8.039748   98.815388
1164539  37.519314 -121.991742
1164540  37.550730 -122.047649
1164541  37.521400 -122.002262
1164542  37.548367 -121.989194
1164543  37.526711 -121.997595
1164544  37.525914 -122.000607
1164545  37.534071 -121.999408
1164546  37.526154 -122.000429
1164547  37.536533 -122.021059
1164548  37.518793 -121.998276
1164549  37.538636 -122.019144
1164550  37.526635 -121.997550
1164551  37.526635 -121.997550
1164552  37.522189 -122.004070
1164553  37.522377 -122.004735
1164554  37.526711 -122.000513
1164555  37.522527 -122.005202
1164556  37.530799 -122.015335
1164557  37.523095 -122.004770
1164558  37.521393 -121.996245

[1164559 rows x 2 columns]

In [6]:
class STRNNCell(nn.Module):
    
    def __init__(self, hidden_size):
        super(STRNNCell, self).__init__()
        self.hidden_size = hidden_size
        self.weight_ih = nn.Parameter(torch.Tensor(hidden_size, hidden_size)) # C
        self.weight_th_upper = nn.Parameter(torch.Tensor(hidden_size, hidden_size)) # T
        self.weight_th_lower = nn.Parameter(torch.Tensor(hidden_size, hidden_size)) # T
        self.weight_sh_upper = nn.Parameter(torch.Tensor(hidden_size, hidden_size)) # S
        self.weight_sh_lower = nn.Parameter(torch.Tensor(hidden_size, hidden_size)) # S

        self.location_weight = nn.Embedding(loc_cnt, hidden_size)
        self.permanet_weight = nn.Embedding(user_cnt, hidden_size)

        self.sigmoid = nn.Sigmoid()

        self.reset_parameters()

    def reset_parameters(self):
        stdv = 1.0 / math.sqrt(self.hidden_size)
        for weight in self.parameters():
            weight.data.uniform_(-stdv, stdv)

    def forward(self, td_upper, td_lower, ld_upper, ld_lower, loc, hx):
        loc_len = len(loc)
        Ttd = [((self.weight_th_upper*td_upper[i] + self.weight_th_lower*td_lower[i])\
                /(td_upper[i]+td_lower[i])) for i in xrange(loc_len)]
        Sld = [((self.weight_sh_upper*ld_upper[i] + self.weight_sh_lower*ld_lower[i])\
                /(ld_upper[i]+ld_lower[i])) for i in xrange(loc_len)]

        loc = self.location_weight(loc).view(-1,self.hidden_size,1)
#         print("loc:")
#         print(loc)
        loc_vec = torch.sum(torch.cat([torch.mm(Sld[i], torch.mm(Ttd[i], loc[i]))\
                .view(1,self.hidden_size,1) for i in xrange(loc_len)], dim=0), dim=0)
#         print("loc_vec:")
#         print(loc_vec)
        usr_vec = torch.mm(self.weight_ih, hx)
#         print("usr_vec:")
#         print(usr_vec)
        hx = loc_vec + usr_vec # hidden_size x 1
#         print("hx:")
#         print(hx)
        return self.sigmoid(hx)

    def loss(self, user, td_upper, td_lower, ld_upper, ld_lower, loc, dst, hx):
        h_tq = self.forward(td_upper, td_lower, ld_upper, ld_lower, loc, hx)
        p_u = self.permanet_weight(user)
        q_v = self.location_weight(dst)
        output = torch.mm(q_v, (h_tq + torch.t(p_u)))
        print("output:")
        print(output)

        return torch.log(1+torch.exp(torch.neg(output)))

    def validation(self, user, td_upper, td_lower, ld_upper, ld_lower, loc, dst, hx):
        # error exist in distance (ld_upper, ld_lower)
        h_tq = self.forward(td_upper, td_lower, ld_upper, ld_lower, loc, hx)
#         print("h_tq:")
#         print(h_tq)
        p_u = self.permanet_weight(user)
#         print("p_u:")
#         print(p_u)
        user_vector = h_tq + torch.t(p_u)
        ret = torch.mm(self.location_weight.weight, user_vector).data.cpu().numpy()
#         print("ret:")
#         print(ret)
        print("result:")
        print(len(np.argsort(np.squeeze(-1*ret))))
        print(np.argsort(np.squeeze(-1*ret)))
        return np.argsort(np.squeeze(-1*ret))

In [7]:
###############################################################################################
def parameters():
    params = []
    for model in [strnn_model]:
        params += list(model.parameters())

    return params

def print_score(batches, step):
    recall1 = 0.
    recall5 = 0.
    recall10 = 0.
    recall100 = 0.
    recall1000 = 0.
    recall10000 = 0.
    iter_cnt = 0

    for batch in tqdm.tqdm(batches, desc="validation"):
        batch_user, batch_td, batch_ld, batch_loc, batch_dst = batch
        if len(batch_loc) < 3:
            continue
        iter_cnt += 1
        batch_o, target = run(batch_user, batch_td, batch_ld, batch_loc, batch_dst, step=step)
        print(batch_o)
        return batch_o[0]
#         print(target)

        recall1 += target in batch_o[:1]
        recall5 += target in batch_o[:5]
        recall10 += target in batch_o[:10]
        recall100 += target in batch_o[:100]
        recall1000 += target in batch_o[:1000]
        recall10000 += target in batch_o[:10000]

    print("recall@1: ", recall1/iter_cnt, flush=True)
    print("recall@5: ", recall5/iter_cnt, flush=True)
    print("recall@10: ", recall10/iter_cnt, flush=True)
    print("recall@100: ", recall100/iter_cnt, flush=True)
    print("recall@1000: ", recall1000/iter_cnt, flush=True)
    print("recall@10000: ", recall10000/iter_cnt, flush=True)

In [8]:
###############################################################################################
def run(user, td, ld, loc, dst, step):

    optimizer.zero_grad()

    seqlen = len(td)
    user = Variable(torch.from_numpy(np.asarray([user]))).type(ltype)

    #neg_loc = Variable(torch.FloatTensor(1).uniform_(0, len(poi2pos)-1).long()).type(ltype)
    #(neg_lati, neg_longi) = poi2pos.get(neg_loc.data.cpu().numpy()[0])
    rnn_output = h_0
    for idx in xrange(seqlen-1):
        td_upper = Variable(torch.from_numpy(np.asarray(up_time-td[idx]))).type(ftype)
        td_lower = Variable(torch.from_numpy(np.asarray(td[idx]-lw_time))).type(ftype)
        ld_upper = Variable(torch.from_numpy(np.asarray(up_dist-ld[idx]))).type(ftype)
        ld_lower = Variable(torch.from_numpy(np.asarray(ld[idx]-lw_dist))).type(ftype)
        location = Variable(torch.from_numpy(np.asarray(loc[idx]))).type(ltype)
        rnn_output = strnn_model(td_upper, td_lower, ld_upper, ld_lower, location, rnn_output)#, neg_lati, neg_longi, neg_loc, step)

    td_upper = Variable(torch.from_numpy(np.asarray(up_time-td[-1]))).type(ftype)
    td_lower = Variable(torch.from_numpy(np.asarray(td[-1]-lw_time))).type(ftype)
    ld_upper = Variable(torch.from_numpy(np.asarray(up_dist-ld[-1]))).type(ftype)
    ld_lower = Variable(torch.from_numpy(np.asarray(ld[-1]-lw_dist))).type(ftype)
    location = Variable(torch.from_numpy(np.asarray(loc[-1]))).type(ltype)

    if step > 1:
        return strnn_model.validation(user, td_upper, td_lower, ld_upper, ld_lower, location, dst[-1], rnn_output), dst[-1]

    destination = Variable(torch.from_numpy(np.asarray([dst[-1]]))).type(ltype)
    J = strnn_model.loss(user, td_upper, td_lower, ld_upper, ld_lower, location, destination, rnn_output)#, neg_lati, neg_longi, neg_loc, step)

    J.backward()
    optimizer.step()

    return J.data.cpu().numpy()

def save_checkpoint(state, is_best, filename='./checkpoint.pth.tar'):
    """Save checkpoint if a new best is achieved"""
    if is_best:
        print ("=> Saving a new best", flush=True)
        torch.save(state, filename)  # save checkpoint
    else:
        print ("=> Validation Accuracy did not improve", flush=True)

In [9]:
strnn_model = STRNNCell(dim).cuda()
optimizer = torch.optim.SGD(parameters(), lr=learning_rate, momentum=momentum, weight_decay=reg_lambda)
strnn_model.load_state_dict(torch.load('./checkpoint.pth.tar')['state_dict'])

In [10]:
def evaluation(train_file = "demo.txt"):
    print("Loading data …")
    train_user, train_td, train_ld, train_loc, train_dst = data_loader.treat_prepro(train_file, step=1)
    # strnn_model = STRNNCell(dim).cuda()
    
#     checkpoint = torch.load('./checkpoint.pth.tar', map_location='cpu')
    
    train_batches = list(zip(train_user, train_td, train_ld, train_loc, train_dst))
#     print(train_batches)
    output = print_score(train_batches, 3)
    print(output)
    print(type(output))
    id2lalo = pd.read_csv("id2latilongi.csv")
    print(id2lalo.size)
    return id2lalo.iloc[output]

In [11]:
evaluation()

validation:   0%|          | 0/1 [00:00<?, ?it/s]

Loading data …
result:
1115406
[ 20292     87   2047 ... 396983 313118 664247]
[ 20292     87   2047 ... 396983 313118 664247]
20292
<class 'numpy.int64'>


2329118


lati      21.292655
longi   -157.852280
Name: 20292, dtype: float64

In [12]:
id2lalo = pd.read_csv("id2latilongi.csv")
id2lalo

lati       longi
0        30.235909  -97.795140
1        30.269103  -97.749395
2        30.255731  -97.763386
3        30.263418  -97.757597
4        30.274292  -97.740523
5        30.261599  -97.758581
6        30.267910  -97.749312
7        30.281120  -97.745211
8        40.643885  -73.782806
9        40.741374  -73.988105
10       40.741388  -73.989455
11       40.724910  -73.994621
12       40.729768  -73.998535
13       40.728527  -73.996868
14       40.741747  -73.993421
15       40.734193  -74.004164
16       40.742512  -74.006031
17       40.742396  -74.007543
18       40.735885  -74.004968
19       40.727525  -73.985399
20       40.756880  -73.986225
21       40.707417  -74.011363
22       40.707173  -74.010545
23       40.707071  -74.011953
24       40.705823  -73.996696
25       40.769378  -73.963083
26       40.780805  -73.976473
27       40.731724  -74.003338
28       40.730869  -73.997566
29       40.742201  -73.987995
...            ...         ...
1164529  51.999576    8.502936
1164530  51.991815    8.493454
1164531  51.989664    8.506508
1164532  52.023326    8.527240
1164533  53.552376   10.006782
1164534  53.795523    9.428444
1164535  54.754836    8.288261
1164536  13.823481  100.558398
1164537  13.765701  100.537731
1164538   8.039748   98.815388
1164539  37.519314 -121.991742
1164540  37.550730 -122.047649
1164541  37.521400 -122.002262
1164542  37.548367 -121.989194
1164543  37.526711 -121.997595
1164544  37.525914 -122.000607
1164545  37.534071 -121.999408
1164546  37.526154 -122.000429
1164547  37.536533 -122.021059
1164548  37.518793 -121.998276
1164549  37.538636 -122.019144
1164550  37.526635 -121.997550
1164551  37.526635 -121.997550
1164552  37.522189 -122.004070
1164553  37.522377 -122.004735
1164554  37.526711 -122.000513
1164555  37.522527 -122.005202
1164556  37.530799 -122.015335
1164557  37.523095 -122.004770
1164558  37.521393 -121.996245

[1164559 rows x 2 columns]

In [5]:
len(train_time)

42241

In [8]:
train_lati

[[30.248923845,
  39.2974431129,
  38.9852462167,
  39.0935326667,
  39.09325785,
  39.0004469333,
  39.0019311833,
  30.2679095833,
  30.2691029532,
  37.7953388902,
  30.2448597206,
  30.26485415,
  30.2510462058,
  30.2691029532,
  30.2138611893,
  30.26485415,
  30.2510314833,
  30.2691029532,
  30.2794862333,
  30.2637747742,
  30.2624620667,
  32.8974616458,
  37.6163560649,
  37.7826046833,
  37.7831295924,
  37.7815086,
  37.7831295924,
  37.7831295924,
  37.7854359476,
  37.7825583,
  37.7826046833,
  37.7614446392,
  37.7881916086,
  37.7857173715,
  37.7825583,
  37.7795577,
  37.7864788714,
  37.7831295924,
  39.0369789909,
  38.9989524833,
  39.05274305,
  30.244761,
  30.2510462058,
  30.2691029532,
  30.244761,
  30.2691029532,
  30.26280055,
  30.2541414667,
  30.2725313677,
  30.2679095833,
  30.2662396721,
  30.2510314833,
  37.6163560649,
  37.5370606667,
  30.2015573297,
  30.26175155,
  30.2638859739,
  30.2510462058,
  30.26406815,
  30.2679095833,
  30.26485415,


In [2]:
class JsonEncoder(json.JSONEncoder):

    def default(self, obj):
        if isinstance(obj, np.integer):
            return int(obj)
        elif isinstance(obj, np.floating):
            return float(obj)
        elif isinstance(obj, np.ndarray):
            return obj.tolist()
        elif isinstance(obj, datetime):                                 
            return obj.__str__()
        else:
            return super(MyEncoder, self).default(obj)

def save_dict(filename, dic):
    '''save dict into json file'''
    with open(filename,'w') as json_file:
        json.dump(dic, json_file, ensure_ascii=False, cls=JsonEncoder)

def load_dict(filename):
    '''load dict from json file'''
    with open(filename,"r") as json_file:
        dic = json.load(json_file)
    return dic

In [6]:
user_cnt

42242

In [7]:
poi2id

{22847: 0,
 420315: 1,
 316637: 2,
 16516: 3,
 5535878: 4,
 15372: 5,
 21714: 6,
 153505: 7,
 23261: 8,
 16907: 9,
 12973: 10,
 341255: 11,
 260957: 12,
 1933724: 13,
 105068: 14,
 34817: 15,
 27836: 16,
 15079: 17,
 22806: 18,
 1365909: 19,
 11844: 20,
 11742: 21,
 19822: 22,
 15169: 23,
 11794: 24,
 1567837: 25,
 35513: 26,
 87914: 27,
 16397: 28,
 17710: 29,
 60450: 30,
 12313: 31,
 34484: 32,
 49215: 33,
 16431: 34,
 18417: 35,
 1151119: 36,
 4256132: 37,
 211286: 38,
 539065: 39,
 15590: 40,
 121955: 41,
 25151: 42,
 1145567: 43,
 46946: 44,
 24276: 45,
 3842712: 46,
 17602: 47,
 17236: 48,
 8964: 49,
 8938: 50,
 19224: 51,
 157923: 52,
 18329: 53,
 17526: 54,
 232292: 55,
 64830: 56,
 9263: 57,
 1576090: 58,
 9223: 59,
 9313: 60,
 1067829: 61,
 480992: 62,
 9508: 63,
 2587606: 64,
 2587024: 65,
 11934: 66,
 9225: 67,
 9241: 68,
 9410: 69,
 19542: 70,
 13338: 71,
 9153: 72,
 202692: 73,
 22765: 74,
 14515: 75,
 14608: 76,
 15478: 77,
 11368: 78,
 20922: 79,
 15245: 80,
 140363: 81

In [43]:
save_dict("poi2id.txt",poi2id)

In [67]:
train_inf = pd.DataFrame({"user":train_user,"time":train_time,"lati":train_lati,"longi":train_longi,"loc":train_loc})

In [38]:
train_inf.to_csv("train_inf.csv")

In [39]:
valid_inf = pd.DataFrame({"user":valid_user,"time":valid_time,"lati":valid_lati,"longi":valid_longi,"loc":valid_loc})

In [40]:
valid_inf.to_csv("valid_inf.csv")

In [41]:
test_inf = pd.DataFrame({"user":test_user,"time":test_time,"lati":test_lati,"longi":test_longi,"loc":test_loc})

In [42]:
test_inf.to_csv("test_inf.csv")

## 预处理后的数据

In [81]:
poi2id = load_dict("poi2id.txt")

In [82]:
poi2id

{'22847': 0,
 '420315': 1,
 '316637': 2,
 '16516': 3,
 '5535878': 4,
 '15372': 5,
 '21714': 6,
 '153505': 7,
 '23261': 8,
 '16907': 9,
 '12973': 10,
 '341255': 11,
 '260957': 12,
 '1933724': 13,
 '105068': 14,
 '34817': 15,
 '27836': 16,
 '15079': 17,
 '22806': 18,
 '1365909': 19,
 '11844': 20,
 '11742': 21,
 '19822': 22,
 '15169': 23,
 '11794': 24,
 '1567837': 25,
 '35513': 26,
 '87914': 27,
 '16397': 28,
 '17710': 29,
 '60450': 30,
 '12313': 31,
 '34484': 32,
 '49215': 33,
 '16431': 34,
 '18417': 35,
 '1151119': 36,
 '4256132': 37,
 '211286': 38,
 '539065': 39,
 '15590': 40,
 '121955': 41,
 '25151': 42,
 '1145567': 43,
 '46946': 44,
 '24276': 45,
 '3842712': 46,
 '17602': 47,
 '17236': 48,
 '8964': 49,
 '8938': 50,
 '19224': 51,
 '157923': 52,
 '18329': 53,
 '17526': 54,
 '232292': 55,
 '64830': 56,
 '9263': 57,
 '1576090': 58,
 '9223': 59,
 '9313': 60,
 '1067829': 61,
 '480992': 62,
 '9508': 63,
 '2587606': 64,
 '2587024': 65,
 '11934': 66,
 '9225': 67,
 '9241': 68,
 '9410': 69,
 '1

In [125]:
train_inf = pd.read_csv("train_inf.csv")
train_user = train_inf["user"].tolist()
train_time = train_inf["time"].tolist()
train_lati = train_inf["lati"].tolist()
train_longi = train_inf["longi"].tolist()
train_loc = train_inf["loc"].tolist()
train_time = list(map(eval,train_time))
train_lati = list(map(eval, train_lati))
train_longi = list(map(eval, train_longi))
train_loc = list(map(eval, train_loc))

In [126]:
valid_inf = pd.read_csv("valid_inf.csv")
valid_user = valid_inf["user"].tolist()
valid_time = valid_inf["time"].tolist()
valid_lati = valid_inf["lati"].tolist()
valid_longi = valid_inf["longi"].tolist()
valid_loc = valid_inf["loc"].tolist()
valid_time = list(map(eval, valid_time))
valid_lati = list(map(eval, valid_lati))
valid_longi = list(map(eval, valid_longi))
valid_loc = list(map(eval, valid_loc))

In [127]:
test_inf = pd.read_csv("test_inf.csv")
test_user = test_inf["user"].tolist()
test_time = test_inf["time"].tolist()
test_lati = test_inf["lati"].tolist()
test_longi = test_inf["longi"].tolist()
test_loc = test_inf["loc"].tolist()
test_time = list(map(eval, test_time))
test_lati = list(map(eval, test_lati))
test_longi = list(map(eval, test_longi))
test_loc = list(map(eval, test_loc))

In [131]:
user_cnt = len(train_inf) + 1

In [9]:
print("User/Location: {:d}/{:d}".format(user_cnt, len(poi2id)))
print("Types:",type(user_cnt), type(poi2id), type(train_user), type(train_time), type(train_lati), type(train_longi), type(train_loc), type(valid_user), type(valid_time), type(valid_lati), type(valid_longi), type(valid_loc), type(test_user), type(test_time), type(test_lati), type(test_longi), type(test_loc))

User/Location: 42242/1164559
Types: <class 'int'> <class 'dict'> <class 'list'> <class 'list'> <class 'list'> <class 'list'> <class 'list'> <class 'list'> <class 'list'> <class 'list'> <class 'list'> <class 'list'> <class 'list'> <class 'list'> <class 'list'> <class 'list'> <class 'list'>


In [10]:
ftype = torch.cuda.FloatTensor
ltype = torch.cuda.LongTensor

In [12]:
def run(user, time, lati, longi, loc, step):

    user = Variable(torch.from_numpy(np.asarray([user]))).type(ltype)
    time = Variable(torch.from_numpy(np.asarray(time))).type(ftype)
    lati = Variable(torch.from_numpy(np.asarray(lati))).type(ftype)
    longi = Variable(torch.from_numpy(np.asarray(longi))).type(ftype)
    loc = Variable(torch.from_numpy(np.asarray(loc))).type(ltype)

    rnn_output = strnn_model(user, time, lati, longi, loc, step)#, neg_lati, neg_longi, neg_loc, step)
    return rnn_output

In [13]:
strnn_model = STRNNModule().cuda()

In [14]:
print("Making train file...")
f = open("./prepro_train_%s.txt"%lw_time, 'w')
# Training
train_batches = list(zip(train_time, train_lati, train_longi, train_loc))
for j, train_batch in enumerate(tqdm.tqdm(train_batches, desc="train")):
    batch_time, batch_lati, batch_longi, batch_loc = train_batch#inner_batch)
    model = run(train_user[j], batch_time, batch_lati, batch_longi, batch_loc, step=1)
    print(type(model))
f.close()

Making train file...


train:   0%|          | 0/42241 [00:00<?, ?it/s]


IndexError: too many indices for array

In [ ]:
print "Making valid file..."
f = open("./prepro_valid_%s.txt"%lw_time, 'w')
# Eavludating
valid_batches = list(zip(valid_time, valid_lati, valid_longi, valid_loc))
for j, valid_batch in enumerate(tqdm.tqdm(valid_batches, desc="valid")):
    batch_time, batch_lati, batch_longi, batch_loc = valid_batch#inner_batch)
    run(valid_user[j], batch_time, batch_lati, batch_longi, batch_loc, step=2)
f.close()

In [ ]:
print "Making test file..."
f = open("./prepro_test_%s.txt"%lw_time, 'w')
# Testing
test_batches = list(zip(test_time, test_lati, test_longi, test_loc))
for j, test_batch in enumerate(tqdm.tqdm(test_batches, desc="test")):
    batch_time, batch_lati, batch_longi, batch_loc = test_batch#inner_batch)
    run(test_user[j], batch_time, batch_lati, batch_longi, batch_loc, step=3)
f.close()
